## STEP 1. 형태소 분석기를 이용하여 품사에 따라 해당 단어를 추출하기

- 명사만 추출 `nouns.txt`
- 명사, 동사 추출 `nouns_verbs.txt`
- 명사, 동사, 형용사 추출 `nouns_verbs_adjectives.txt`

In [2]:
import os

from konlpy.tag import Okt
okt = Okt()
tokenized = []
with open(os.getenv('HOME')+'/aiffel/weat/synopsis.txt', 'r') as file:
    while True:
        line = file.readline()
        if not line: break
        words = okt.pos(line, stem=True, norm=True)
        res = []
        for w in words:
            if w[1] in ["Noun", "Verb"]:      # "Adjective", "Verb" 등을 포함할 수도 있습니다.
                res.append(w[0])    # 명사일 때만 tokenized 에 저장하게 됩니다. 
        tokenized.append(res)

## STEP 2. 추출된 결과로 embedding model 만들기

In [3]:
from gensim.models import Word2Vec

# tokenized에 담긴 데이터를 가지고 나만의 Word2Vec을 생성합니다. (Gensim 4.0 기준)
model = Word2Vec(tokenized, vector_size=100, window=5, min_count=3, sg=0)  
model.wv.most_similar(positive=['영화'])

[('작품', 0.8634408116340637),
 ('다큐멘터리', 0.8370234370231628),
 ('영화로', 0.7895338535308838),
 ('드라마', 0.7874850034713745),
 ('코미디', 0.7387531399726868),
 ('주제', 0.7315828800201416),
 ('스토리', 0.7300704717636108),
 ('설정', 0.7247071266174316),
 ('영상', 0.720420241355896),
 ('실화', 0.7202526926994324)]

## STEP 3. target, attribute 단어 셋 만들기

In [4]:
import os
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
from konlpy.tag import Okt

art_txt = 'synopsis_art.txt'
gen_txt = 'synopsis_gen.txt'

def read_token(file_name):
    okt = Okt()
    result = []
    with open(os.getenv('HOME')+'/aiffel/weat/'+file_name, 'r') as fread: 
        print(file_name, '파일을 읽고 있습니다.')
        while True:
            line = fread.readline() 
            if not line: break 
            tokenlist = okt.pos(line, stem=True, norm=True) 
            for word in tokenlist:
                if word[1] in ["Noun", "Verb"]:#, "Adjective", "Verb"]:
                    result.append((word[0])) 
    return ' '.join(result)

### target 단어 추출

In [5]:
art = read_token(art_txt)
gen = read_token(gen_txt)

synopsis_art.txt 파일을 읽고 있습니다.
synopsis_gen.txt 파일을 읽고 있습니다.


In [6]:
art

'사운드 엔지니어 상우 유지태 분 늘다 치매 걸리다 할머니 백성희 분 오다 시절 상처 하다 아버지 박인환 분 고모 신신애 분 오다 살 겨울 그 지방 방송국 라디오 은수 이영애 분 를 만나다 자연 소리 채집 하다 틀어주다 라디오 프로그램 준비 하다 은수 상우 녹음 여행 떠나다 가까워지다 두 사람 날 은수 아파트 밤 보내다 쉬다 사랑 빠지다 두 사람 상우 주체 하다 수 정도 그녀 빨다 들다 겨울 만난 두 사람 관계 봄 지나 여름 맞이 하다 삐걱 거 린다 이혼 경험 은수 상우 결혼 하다 생각 표정 내비 치다 사랑 묻다 상우 은수 헤어지다 단호 하다 말 하다 것 않다 사랑 그 사실 받아들이다 하다 상우 어찌 하다 바르다 모르다 은수 잊다 하다 상우 미련 집착 감정 이기 못 서울 강릉 간다 태희 배두나 분 깍쟁이 혜주 이요원 분 그림 자다 그리다 지영 옥 지영 분 쌍둥이 비류 이은실 분 오다 온조 이은주 분 늘다 단짝 친구 늘 하다 그 스무 살이 되다 길이 달라지다 증권 회사 입사 혜주 커리어우먼 야심 키우다 미술 재능 지영은 유학 꿈꾸다 한편 태희 봉사활동 알 되다 뇌성마비 시인 날 지영 길 잃다 새끼 고양이 티티 만나다 스무 살 그녀 삶 고양이 하다 마리 끼어들다 되다 혼자 쉬다 마음 열다 않다 동물 고양이 고양이 닮다 스무 살 그녀 고양이 티티 하다 시간 동안 삶다 예상 못 방향 흘러가다 마침내 그녀 해결 책 찾다 되다 몽상가 태희 야심 혜주 아웃사이더 지영 마지막 고양이 부탁 받다 사람 누구 이다 산타모니카 이르다 도로 홀랜드 드라이브 날 밤 차 사고 발생 하다 사고 가까스로 살아나다 리타 로라 해링 분 늘다 기억상실증 걸리다 채 근처 하다 빌라 숨다 들어가다 한편 헐리웃 스타 꿈 안고 도착 베티 나오미 왓츠 분 늘다 이모 집 방문 곳 숨다 리타 발견 하다 베티 자신 미래 보장 하다 줄 아담 케셔 감독 만남 제 치다 두다 리타 돕기 위해 그녀 남다 기억 단서 이안 인물 찾다 나서다 하다 낮 윙 키스 식당 대다 곳 허브 만나다 자신 꾼 악몽 대해 이야기 이 윙 키

In [7]:
gen

'유사 연령 성별 빈부 차이 정치 입장 불문 이다 국민 통합 하다 온 애국심 성역 일침 가하다 다큐멘터리 재작년 전국 민족 민주 유가족 협의 회의 장기 농성 다루다 인상 다큐멘터리 민들레 를 만들다 독립영화 집단 눈사람 이 우리 사회 구석구석 발 돌아다니다 애국심 민족주의 강요 되다 현장 발굴 하다 카메라 담다 박홍 서강대 명예 총장 이도형 한국 논단 발행 축구 해설 신문선 홍세화 박노해 등 사회 각계 스타 들이다 등장 하다 저 신념 토 하다 감독 순 최하 동하 이 작품 위해 명 인터뷰 하다 하다 올해 독립영화 수상 민족 국가 란 공동체 권력 부르다 얻다 자 나아가다 민족 국가 란 공동체 얻다 신분 부귀 그 자손 대물리다 자 민족 국가 란 공동체 유지 하다 하다 자 따라서 민족 국가 란 공동체 당위 성과 개인 가치 초월 하다 그 존엄성 끝 창조 되다 뇌 하다 자 종국 민족 국가 란 공동체 해 태내 세뇌 되다 모든 이 삶 행동 자기 복제 되다 순환 고리 영생 하다 애국 원동력 그 순환 골 오다 엽기 살인 사건 발생 장소 관광 하다 투어 팀 그 팀 관광객 살인 사건 관련 하다 히스테리 컬 반응 보이다 과연 이 정체 제 발라 돌 리드 국제 영화제 스페인 인도 등 아시아 식민지 처음 발 디디다 뒤 여행 경영 하다 이 과연 누구 이다 과거 이미지 이민 인종 문제 오리엔탈리즘 이 충돌 현재 공명 제 인디다큐페스티발 홀로 살아가다 미국 할머니 한국 할머니 이야기 공원 가끔 마주치다 되다 그 비록 언어 소통 어려움 겪다 시간 흘러가다 따르다 서로 가까워지다 그 외로움 우정 공유 하다 되다 겨울 지나다 봄 오다 때 길가 민들레 홀씨 삶 이치 말 해주다 하다 할머니 주위 맴돈다 연출 의도 나 노년 이르다 사람 언어 문화 다른 삶 접 하다 때 헤치다 나가다 문화 인종 벽 넘어서다 우리 인간 늘다 누구 질문 통해 모든 인간 지니 질 찾다 하다 전설 금고 털이범 닉 웰즈 이제 은퇴 후 자신 여자친구 앤 재즈 클럽 운영 하다 합법 생활 하다 몬트리올 정착 하다 하다 계획 롭 진행 되다

In [8]:
vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform([art, gen])

In [9]:
m1 = X[0].tocoo()   # art를 TF-IDF로 표현한 sparse matrix를 가져옵니다. 
m2 = X[1].tocoo()   # gen을 TF-IDF로 표현한 sparse matrix를 가져옵니다. 

w1 = [[i, j] for i, j in zip(m1.col, m1.data)]
w2 = [[i, j] for i, j in zip(m2.col, m2.data)]

w1.sort(key=lambda x: x[1], reverse=True)   #art를 구성하는 단어들을 TF-IDF가 높은 순으로 정렬합니다. 
w2.sort(key=lambda x: x[1], reverse=True)   #gen을 구성하는 단어들을 TF-IDF가 높은 순으로 정렬합니다. 

print('예술영화를 대표하는 단어들:')
for i in range(100):
    print(vectorizer.get_feature_names()[w1[i][0]], end=', ')

print('\n')
    
print('일반영화를 대표하는 단어들:')
for i in range(100):
    print(vectorizer.get_feature_names()[w2[i][0]], end=', ')

예술영화를 대표하는 단어들:
하다, 되다, 그녀, 

/opt/conda/lib/python3.9/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


자신, 시작, 위해, 사랑, 않다, 사람, 늘다, 받다, 오다, 영화, 친구, 가다, 만나다, 남자, 찾다, 이다, 떠나다, 가족, 이야기, 되어다, 마을, 보다, 사건, 마음, 세상, 아버지, 아이, 엄마, 모든, 빠지다, 여자, 버리다, 대한, 서로, 과연, 다시, 시간, 아들, 소녀, 보내다, 느끼다, 아내, 살다, 다른, 싶다, 모르다, 사이, 영화제, 세계, 사실, 크다, 하나, 들다, 만들다, 잃다, 점점, 남편, 감독, 어리다, 여행, 인생, 발견, 모두, 순간, 우리, 가장, 찾아오다, 마지막, 생활, 아빠, 죽다, 지키다, 모습, 통해, 죽음, 기억, 비밀, 학교, 말다, 음악, 한편, 소년, 살아가다, 생각, 도시, 명의, 나타나다, 사고, 결혼, 전쟁, 돌아오다, 때문, 위기, 사라지다, 이제, 최고, 이자, 

일반영화를 대표하는 단어들:
하다, 되다, 자신, 그녀, 영화제, 위해, 않다, 사람, 시작, 국제, 영화, 받다, 친구, 사랑, 남자, 오다, 늘다, 가다, 이야기, 이다, 되어다, 보다, 만나다, 찾다, 대한, 서울, 여자, 사건, 남편, 아이, 가족, 아버지, 떠나다, 버리다, 다른, 들다, 마을, 시간, 엄마, 아들, 모든, 만들다, 단편, 마음, 살다, 사실, 다시, 보내다, 세계, 모습, 빠지다, 작품, 통해, 생각, 서로, 싶다, 느끼다, 세상, 발견, 감독, 아내, 관계, 소녀, 사이, 시키다, 어리다, 하나, 크다, 우리, 애니메이션, 때문, 모르다, 죽다, 여성, 주다, 말다, 죽음, 과연, 점점, 인간, 생활, 한편, 잃다, 결혼, 상황, 모두, 내다, 기억, 이르다, 나타나다, 명의, 소년, 돌아오다, 나가다, 여행, 찾아오다, 가장, 간다, 순간, 이제, 

In [ ]:
# 중복 제거
n = 15

# w1에만 있고 w2에는 없는, 예술영화를 잘 대표하는 단어를 15개 추출한다.
target_art, target_gen = [], []
for i in range(100):
    if (w1_[i] not in w2_) and (w1_[i] in model.wv): target_art.append(w1_[i])
    if len(target_art) == n: break 

# w2에만 있고 w1에는 없는, 일반영화를 잘 대표하는 단어를 15개 추출한다.
for i in range(100):
    if (w2_[i] not in w1_) and (w2_[i] in model.wv): target_gen.append(w2_[i])
    if len(target_gen) == n: break

### attribute 단어 추출 

In [ ]:
#파일 불러와서 TF-IDF 생성
genre_txt = ['synopsis_SF.txt', 'synopsis_family.txt', 'synopsis_show.txt', 'synopsis_horror.txt', 'synopsis_etc.txt', 
             'synopsis_documentary.txt', 'synopsis_drama.txt', 'synopsis_romance.txt', 'synopsis_musical.txt', 
             'synopsis_mystery.txt', 'synopsis_crime.txt', 'synopsis_historical.txt', 'synopsis_western.txt', 
             'synopsis_adult.txt', 'synopsis_thriller.txt', 'synopsis_animation.txt', 'synopsis_action.txt', 
             'synopsis_adventure.txt', 'synopsis_war.txt', 'synopsis_comedy.txt', 'synopsis_fantasy.txt']
genre_name = ['SF', '가족', '공연', '공포(호러)', '기타', '다큐멘터리', '드라마', '멜로로맨스', '뮤지컬', '미스터리', '범죄', '사극', '서부극(웨스턴)',
         '성인물(에로)', '스릴러', '애니메이션', '액션', '어드벤처', '전쟁', '코미디', '판타지']
output_genre_txt = [txt.strip('.txt')+'nouns_verbs.txt' for txt in genre_txt]

'''
save_tokens(art_txt, output_art_txt)
save_tokens(gen_txt, output_gen_txt)
'''

genre = []
for file_name in genre_txt:
    genre.append(save_tokens(file_name))
vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform(genre)

In [ ]:
m = [X[i].tocoo() for i in range(X.shape[0])]

w = [[[i, j] for i, j in zip(mm.col, mm.data)] for mm in m]

for i in range(len(w)):
    w[i].sort(key=lambda x: x[1], reverse=True)
attributes = []
for i in range(len(w)):
    print(genre_name[i], end=': ')
    attr = []
    j = 0
    while (len(attr) < 15):
        if vectorizer.get_feature_names()[w[i][j][0]] in model.wv:
            attr.append(vectorizer.get_feature_names()[w[i][j][0]])
            print(vectorizer.get_feature_names()[w[i][j][0]], end=', ')
        j += 1
    attributes.append(attr)
    print()

## STEP 4. WEAT score 계산과 시각화

In [ ]:
from numpy import dot
from numpy.linalg import norm
# WEAT score function
def cos_sim(i, j):
    return dot(i, j.T)/(norm(i)*norm(j))
def s(w, A, B):
    c_a = cos_sim(w, A)
    c_b = cos_sim(w, B)
    mean_A = np.mean(c_a, axis=-1)
    mean_B = np.mean(c_b, axis=-1)
    return mean_A - mean_B #, c_a, c_b
def weat_score(X, Y, A, B):
    
    s_X = s(X, A, B)
    s_Y = s(Y, A, B)

    mean_X = np.mean(s_X)
    mean_Y = np.mean(s_Y)
    
    std_dev = np.std(np.concatenate([s_X, s_Y], axis=0))
    
    return  (mean_X-mean_Y)/std_dev

In [ ]:
# embedding model과 단어 셋으로 WEAT score 구해보기
matrix = [[0 for _ in range(len(genre_name))] for _ in range(len(genre_name))]
X = np.array([model.wv[word] for word in target_art])
Y = np.array([model.wv[word] for word in target_gen])

for i in range(len(genre_name)-1):
    for j in range(i+1, len(genre_name)):
        A = np.array([model.wv[word] for word in attributes[i]])
        B = np.array([model.wv[word] for word in attributes[j]])
        matrix[i][j] = weat_score(X, Y, A, B)
        
for i in range(len(genre_name)-1):
    for j in range(i+1, len(genre_name)):
        print(genre_name[i], genre_name[j],matrix[i][j])

In [ ]:
# 시각화
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

def plot_heatmap(matrix, genre_name, title, save=True):
    np.random.seed(0)
    # 한글 지원 폰트
    sns.set(font='NanumGothic')

    # 마이너스 부호 
    plt.rcParams['axes.unicode_minus'] = False

    fig, ax = plt.subplots(figsize=(15,13))
    sns.heatmap(matrix, xticklabels=genre_name, yticklabels=genre_name, annot=True, cmap='RdYlGn_r', ax=ax)

    ax.set_title(title, fontsize=20, pad=20)
    if save:
        plt.savefig('heatmap_'+title+'.png', bbox_inches='tight')

    plt.show()
    
plot_heatmap(matrix, genre_name, 'simple_tfidf', False)